In [4]:
import pandas as pd
import plotly.graph_objects as go

# 讀取數據
file_path = 'TDCS_M06A_20240523_090000.csv'
data = pd.read_csv(file_path)#, nrows=200)

# 確認欄位名稱
data.columns = ['VehicleType', 'DetectionTime_O', 'GantryID_O', 'DetectionTime_D', 'GantryID_D', 'TripLength', 'TripEnd', 'TripInformation']

# 轉換時間格式
data['DetectionTime_O'] = pd.to_datetime(data['DetectionTime_O'])
data['DetectionTime_D'] = pd.to_datetime(data['DetectionTime_D'])

# 只取GantryID_O開頭是01結尾是S的資料
# data = data[data['GantryID_O'].str.startswith('01')]
data = data[data['GantryID_O'].str.endswith('S')]
data = data[data['GantryID_D'].str.endswith('S')]

# 移除重複記錄
data_cleaned = data.drop_duplicates()


gantry_filepath = 'gantryID.csv'
gantryList = pd.read_csv(gantry_filepath)

gantryList.columns = ['line','direction','gantryNo','gantryID','src','dest','mille','carPrice','trunkPrice','largeTruckPrice','lat','lng']
# 新增name並將名稱轉換為[src]_[dest]
gantryList['name'] = gantryList['src'] + '_' + gantryList['dest']

# 提取站點流動信息
flows = []
for trip_info in data_cleaned['TripInformation']:
    stations = trip_info.split('; ')
    for i in range(len(stations) - 1):
        source = stations[i].split('+')[1]
        target = stations[i + 1].split('+')[1]
        flows.append((source, target))

# 構建 Sankey 圖所需數據
sources = []
targets = []
values = []

flow_dict = {}
for source, target in flows:
    if (source, target) in flow_dict:
        flow_dict[(source, target)] += 1
    else:
        flow_dict[(source, target)] = 1

for key, value in flow_dict.items():
    sources.append(key[0])
    targets.append(key[1])
    values.append(value)

# 創建節點列表
all_nodes = list(set(sources + targets))
node_indices = {node: idx for idx, node in enumerate(all_nodes)}

# 創建 Sankey 圖
fig = go.Figure(data=[go.Sankey(
    node=dict(
        pad=15,
        thickness=20,
        line=dict(color="black", width=0.5),
        label=all_nodes,
    ),
    link=dict(
        source=[node_indices[source] for source in sources],
        target=[node_indices[target] for target in targets],
        value=values,
    ))])

fig.update_layout(title_text="車輛在不同站點之間的流動 Sankey 圖", font_size=10)
fig.write_image("sankey.png")
fig.write_html("sankey.html")


In [3]:
file_path = 'TDCS_M06A_20240523_090000.csv'

# 讀取CSV文件的前100行
df = pd.read_csv(file_path, nrows=100)

# 打印前5行數據進行檢查
print(df.head())

f03_df = df[df['GantryID_O'].astype(str).str.startswith('03')]

print(f03_df.head())


   VehicleType  DetectionTime_O GantryID_O  DetectionTime_D GantryID_D  \
0           31  2024/5/23 09:35   01F3535S  2024/5/23 09:35   01F3535S   
1           31  2024/5/23 09:00   01F0532S  2024/5/23 09:03   01F0557S   
2           32  2024/5/23 09:02   03F0447S  2024/5/23 09:02   03F0447S   
3           32  2024/5/23 09:15   01F0633S  2024/5/23 09:20   01F0681S   
4           31  2024/5/23 09:39   01F0153N  2024/5/23 09:47   01F0061N   

   TripLength TripEnd                                    TripInformation  
0         6.8       Y                       2024-05-23 09:35:09+01F3535S  
1         4.5       Y  2024-05-23 09:00:53+01F0532S; 2024-05-23 09:03...  
2         3.5       Y                       2024-05-23 09:02:51+03F0447S  
3         6.8       Y  2024-05-23 09:15:58+01F0633S; 2024-05-23 09:18...  
4        11.8       Y  2024-05-23 09:39:09+01F0153N; 2024-05-23 09:39...  
    VehicleType  DetectionTime_O GantryID_O  DetectionTime_D GantryID_D  \
2            32  2024/5/23 09:

In [4]:
f03_df.head()

VehicleType  DetectionTime_O GantryID_O  DetectionTime_D GantryID_D  \
2            32  2024/5/23 09:02   03F0447S  2024/5/23 09:02   03F0447S   
5            32  2024/5/23 09:01   03F2260N  2024/5/23 09:08   03F2125N   
6            32  2024/5/23 09:57   03F2129S  2024/5/23 10:04   03F2261S   
7            31  2024/5/23 09:41   03F1128N  2024/5/23 09:41   03F1128N   
12           31  2024/5/23 09:34   03F4232N  2024/5/23 09:37   03F4168N   

    TripLength TripEnd                                    TripInformation  
2          3.5       Y                       2024-05-23 09:02:51+03F0447S  
5         17.3       Y  2024-05-23 09:01:01+03F2260N; 2024-05-23 09:02...  
6         17.3       Y  2024-05-23 09:57:03+03F2129S; 2024-05-23 09:58...  
7          5.4       Y                       2024-05-23 09:41:38+03F1128N  
12         9.3       Y  2024-05-23 09:34:34+03F4232N; 2024-05-23 09:37...

In [5]:
# 將拆分後的列名重新命名
f03_df.loc[:, 'TripInformation'] = f03_df['TripInformation'].apply(lambda x: x.split('; '))

In [6]:
f03_df.head()

VehicleType  DetectionTime_O GantryID_O  DetectionTime_D GantryID_D  \
2            32  2024/5/23 09:02   03F0447S  2024/5/23 09:02   03F0447S   
5            32  2024/5/23 09:01   03F2260N  2024/5/23 09:08   03F2125N   
6            32  2024/5/23 09:57   03F2129S  2024/5/23 10:04   03F2261S   
7            31  2024/5/23 09:41   03F1128N  2024/5/23 09:41   03F1128N   
12           31  2024/5/23 09:34   03F4232N  2024/5/23 09:37   03F4168N   

    TripLength TripEnd                                    TripInformation  
2          3.5       Y                     [2024-05-23 09:02:51+03F0447S]  
5         17.3       Y  [2024-05-23 09:01:01+03F2260N, 2024-05-23 09:0...  
6         17.3       Y  [2024-05-23 09:57:03+03F2129S, 2024-05-23 09:5...  
7          5.4       Y                     [2024-05-23 09:41:38+03F1128N]  
12         9.3       Y  [2024-05-23 09:34:34+03F4232N, 2024-05-23 09:3...